In [6]:
from ipywidgets import FileUpload, Text, Button, Output, VBox
from IPython.display import display
from docx import Document
import re

# Создаем виджеты
upload_widget = FileUpload(accept='.txt', multiple=False)  # Виджет для загрузки файла
output_name_widget = Text(placeholder='Введите название для файла .docx', description='Имя файла:')
process_button = Button(description='Преобразовать')  # Кнопка для запуска преобразования
output_widget = Output()  # Виджет для вывода сообщений

# Функция для обработки файла и сохранения в формате .docx
def process_file(_):
    with output_widget:
        output_widget.clear_output()
        
        # Проверяем, загружен ли файл
        if not upload_widget.value:
            print("Пожалуйста, загрузите файл .txt.")
            return
        
        # Проверяем, указано ли имя для выходного файла
        if not output_name_widget.value.strip():
            print("Пожалуйста, укажите имя для выходного файла .docx.")
            return
        
        # Получаем содержимое файла
        uploaded_files = upload_widget.value  # Это кортеж загруженных файлов
        if not uploaded_files:
            print("Не удалось найти загруженный файл.")
            return
        
        # Извлекаем первый файл
        uploaded_file = list(uploaded_files.values())[0] if isinstance(uploaded_files, dict) else uploaded_files[0]
        content = bytes(uploaded_file['content']).decode('utf-8')  # Преобразуем memoryview в bytes и декодируем
        
        # Создаем новый документ
        doc = Document()
        
        # Регулярное выражение для поиска заголовков "Chapter + номер"
        chapter_pattern = re.compile(r'^Chapter\s+\d+', re.IGNORECASE)
        
        # Разбиваем текст на строки и обрабатываем их
        lines = content.splitlines()
        for line in lines:
            stripped_line = line.strip()
            if chapter_pattern.match(stripped_line):
                doc.add_heading(stripped_line, level=1)
            else:
                doc.add_paragraph(stripped_line)
        
        # Сохраняем документ с указанным именем
        output_file = f"{output_name_widget.value.strip()}.docx"
        doc.save(output_file)
        
        # Выводим сообщение об успешном сохранении
        print(f"Файл успешно преобразован и сохранен как '{output_file}'")

# Привязываем функцию к кнопке
process_button.on_click(process_file)

# Отображаем виджеты
display(VBox([upload_widget, output_name_widget, process_button, output_widget]))
